In [1]:
import json
with open("final_dataset.json", "r") as f:
    final_structure = json.load(f)

In [2]:
difficulties = []
for level, problems in final_structure.items():
    for key, problem_data in problems.items():
        difficulties.append((int(problem_data["difficulty_level"]), (level, key)))

In [3]:
# order by difficulty ascending
difficulties.sort(key=lambda x: x[0])

In [4]:
# split into 3 groups
n = len(difficulties)
group_size = n // 3
easy = difficulties[:group_size]
medium = difficulties[group_size:2*group_size]
hard = difficulties[2*group_size:]

In [5]:
# find average difficulty for each group
easy_avg = sum([x[0] for x in easy]) / len(easy)
medium_avg = sum([x[0] for x in medium]) / len(medium)
hard_avg = sum([x[0] for x in hard]) / len(hard)
print(easy_avg, medium_avg, hard_avg)

1224.954887218045 1529.5112781954888 1827.5037593984962


In [6]:
# print min and max difficulty for each group
print(easy[0], easy[-1])
print(medium[0], medium[-1])
print(hard[0], hard[-1])

(828, ('0', 'SNAPE')) (1417, ('2', 'UNICOURS'))
(1419, ('2', 'EQUALITY')) (1646, ('3', 'CIELDIST'))
(1647, ('3', 'OBTTRNGL')) (3420, ('7', 'NQNF'))


In [7]:
import os
bins = {
    "easy": easy,
    "medium": medium,
    "hard": hard
}
for tag, data in bins.items():
    for entry in data:
        level, key = entry[1]
        problem_data = final_structure[level][key]

        humans_solutions = problem_data["human_solutions"]
        human_solution_1, human_solution_2 = humans_solutions[0]["code"], humans_solutions[1]["code"]
        # ai_solution_1 = problem_data["python_sol"]

        ai_solution_1, ai_solution_2 = problem_data["ai_solutions"]
        assert human_solution_1 != human_solution_2
        assert ai_solution_1 != ai_solution_2

        if not os.path.exists(f"unverified/{tag}"):
            os.makedirs(f"unverified/{tag}")
        with open(f"unverified/{tag}/human_{key}_1.py", "w") as f:
            f.write(human_solution_1)
        with open(f"unverified/{tag}/human_{key}_2.py", "w") as f:
            f.write(human_solution_2)
        with open(f"unverified/{tag}/ai_{key}_1.py", "w") as f:
            f.write(ai_solution_1)
        with open(f"unverified/{tag}/ai_{key}_2.py", "w") as f:
            f.write(ai_solution_2)

In [8]:
with open("unverified/mapping.json", "w") as f:
    json.dump(bins, f, indent=4)

In [9]:
with open("final_successful_dataset.json", "r") as f:
    final_structure = json.load(f)

In [10]:
easy_correct = []
medium_correct = []
hard_correct = []

In [11]:
for tag, data in bins.items():
    for entry in data:
        level, key = entry[1]
        if key not in final_structure[level]:
            continue
        problem_data = final_structure[level][key]
        ai_solutions = problem_data["ai_solutions"]
        if len(ai_solutions) == 0:
            continue
        if tag == "easy":
            easy_correct.append((int(problem_data["difficulty_level"]), (level, key)))
        elif tag == "medium":
            medium_correct.append((int(problem_data["difficulty_level"]), (level, key)))
        else:
            hard_correct.append((int(problem_data["difficulty_level"]), (level, key)))
        if not os.path.exists(f"verified/{tag}"):
            os.makedirs(f"verified/{tag}")

        humans_solutions = problem_data["human_solutions"]
        human_solution_1, human_solution_2 = humans_solutions[0]["code"], humans_solutions[1]["code"]

        for i, ai_solution in enumerate(ai_solutions):
            index = i + 1
            with open(f"verified/{tag}/human_{key}_{index}.py", "w") as f:
                if index == 1:
                    f.write(human_solution_1)
                else:
                    f.write(human_solution_2)
            with open(f"verified/{tag}/ai_{key}_{index}.py", "w") as f:
                f.write(ai_solution)

        # humans_solutions = problem_data["human_solutions"]
        # human_solution_1, human_solution_2 = humans_solutions[0]["code"], humans_solutions[1]["code"]
        # ai_solution_1 = problem_data["python_sol"]
        # with open(f"verified/{tag}/human_{key}_1.py", "w") as f:
        #     f.write(human_solution_1)
        # with open(f"verified/{tag}/ai_{key}_1.py", "w") as f:
        #     f.write(ai_solution_1)

In [12]:
print(len(easy_correct))
print(len(medium_correct))
print(len(hard_correct))

86
48
27


In [7]:
with open("final_successful_dataset.json", "r") as f:
    final_structure_success = json.load(f)
single_solutions_easy = []
single_solutions_medium = []
single_solutions_hard = []
for level, problems in final_structure_success.items():
    for key, problem_data in problems.items(): 
        if len(problem_data["ai_solutions"]) == 1:
            # create list with second element of easy, medium, hard
            list_easy = [x[1] for x in easy]
            list_medium = [x[1] for x in medium]
            list_hard = [x[1] for x in hard]
            if (level, key) in list_easy:
                single_solutions_easy.append((level, key))
            elif (level, key) in list_medium:
                single_solutions_medium.append((level, key))
            elif (level, key) in list_hard:
                single_solutions_hard.append((level, key))
            else:
                print("ERROR")
                print(level, key)

In [8]:
len(single_solutions_easy)+len(single_solutions_medium)+len(single_solutions_hard)

24

In [9]:
import random
random.seed(22)
# random sample 86 easy, 48 medium, 27 hard
count_single_easy = len(single_solutions_easy)
count_single_medium = len(single_solutions_medium)
count_single_hard = len(single_solutions_hard)
count_double_easy = 86 - count_single_easy
count_double_medium = 48 - count_single_medium
count_double_hard = 27 - count_single_hard

single_easy = random.sample(easy, count_single_easy)
single_medium = random.sample(medium, count_single_medium)
single_hard = random.sample(hard, count_single_hard)

# sample double from the remaining only
remaining_easy = [x for x in easy if x not in single_easy]
remaining_medium = [x for x in medium if x not in single_medium]
remaining_hard = [x for x in hard if x not in single_hard]

double_easy = random.sample(remaining_easy, count_double_easy)
double_medium = random.sample(remaining_medium, count_double_medium)
double_hard = random.sample(remaining_hard, count_double_hard)

In [10]:
count_double_medium*2+count_single_medium

91

In [13]:
sampled_bins = {
    "sample_easy": single_easy + double_easy,
    "sample_medium": single_medium + double_medium,
    "sample_hard": single_hard + double_hard
}
import os
import json
with open("final_dataset.json", "r") as f:
    final_structure = json.load(f)
for tag, data in sampled_bins.items():
    for entry in data:
        level, key = entry[1]
        is_single = False
        if tag == "sample_easy":
            if entry in single_easy:
                is_single = True
            else:
                assert entry in double_easy
        elif tag == "sample_medium":
            if entry in single_medium:
                is_single = True
            else:
                assert entry in double_medium
        else:
            if entry in single_hard:
                is_single = True
            else:
                assert entry in double_hard
        problem_data = final_structure[level][key]
        ai_solutions = problem_data["ai_solutions"]
        if len(ai_solutions) == 0:
            continue
        humans_solutions = problem_data["human_solutions"]
        human_solution_1, human_solution_2 = humans_solutions[0]["code"], humans_solutions[1]["code"]

        # ai_solution_1 = problem_data["python_sol"]

        if not os.path.exists(f"verified/{tag}"):
            os.makedirs(f"verified/{tag}")

        for i, ai_solution in enumerate(ai_solutions):
            index = i + 1
            if is_single and index == 2:
                continue
            with open(f"verified/{tag}/human_{key}_{index}.py", "w") as f:
                if index == 1:
                    f.write(human_solution_1)
                else:
                    f.write(human_solution_2)
            with open(f"verified/{tag}/ai_{key}_{index}.py", "w") as f:
                f.write(ai_solution)